In [1]:
import argparse
import json
import logging
import sys
from os.path import join as pjoin

import h5py
import onnx
import torch
import torch.nn.functional as F

#from braindecode.models.deep4 import Deep4Net
from quantized_deep4 import QuantDeep4Net
from braindecode.torch_ext.optimizers import AdamW
from braindecode.torch_ext.util import set_random_seeds

ModuleNotFoundError: No module named 'h5py'

In [3]:
datapath = "./processed_data/KU_mi_smt.h5"
dfile = h5py.File(datapath, 'r')
subj = 6
torch.cuda.set_device(0)
set_random_seeds(seed=20200205, cuda=True)

In [4]:
def get_data(subj):
    dpath = '/s' + str(subj)
    X = dfile[pjoin(dpath, 'X')]
    Y = dfile[pjoin(dpath, 'Y')]
    return X[:], Y[:]

In [5]:
# Get data for within-subject classification
X, Y = get_data(subj)

X_train, Y_train = X[:200], Y[:200]
X_val, Y_val = X[200:300], Y[200:300]
X_test, Y_test = X[300:], Y[300:]

suffix = 's' + str(subj)
n_classes = 1
in_chans = X.shape[1]

# final_conv_length = auto ensures we only get a single output in the time dimension
model = QuantDeep4Net(in_chans=in_chans, n_classes=n_classes,
                 input_time_length=X.shape[2],
                 final_conv_length=1).cuda()

# these are good values for the deep model
optimizer = AdamW(model.parameters(), lr=1 * 0.01, weight_decay=0.5*0.001)
model.compile(loss=F.cross_entropy, optimizer=optimizer, iterator_seed=1, )

model.fit(X_train, Y_train, epochs=5, batch_size=16, scheduler='cosine', 
        validation_data=(X_val, Y_val))#, remember_best_column='valid_loss')

/tmp/home_dir/.local/lib/python3.8/site-packages/braindecode/torch_ext/optimizers.py:70: UserWarning: This overload of add_ is deprecated:
	add_(Number alpha, Tensor other)
Consider using one of the following signatures instead:
	add_(Tensor other, *, Number alpha) (Triggered internally at  /pytorch/torch/csrc/utils/python_arg_parser.cpp:766.)
  exp_avg.mul_(beta1).add_(1 - beta1, grad)


In [6]:
test_loss = model.evaluate(X_test, Y_test)
print(test_loss)

{'loss': 0.07702192664146423, 'misclass': 0.0, 'runtime': 0.0014452934265136719}


In [7]:
from finn.util.basic import make_build_dir
from finn.util.visualization import showInNetron
    
build_dir = "/workspace/finn"

In [8]:
import brevitas.onnx as bo

bo.export_finn_onnx(model.network.cpu(), export_path=build_dir + "/mai_subj6_export.onnx", input_t=torch.randn(1, 62, 1000, 1))

/tmp/home_dir/.local/lib/python3.8/site-packages/brevitas/quant_tensor/__init__.py:74: TracerWarning: torch.tensor results are registered as constants in the trace. You can safely ignore this warning if you use this function to create tensors out of constant variables that would be the same every time you call this function. In any other case, this might cause the trace to be incorrect.
  training = torch.tensor(training, dtype=torch.bool)


ir_version: 6
producer_name: "pytorch"
producer_version: "1.6"
graph {
  node {
    input: "0"
    output: "37"
    name: "Transpose_0"
    op_type: "Transpose"
    attribute {
      name: "perm"
      ints: 0
      ints: 3
      ints: 2
      ints: 1
      type: INTS
    }
  }
  node {
    input: "37"
    input: "38"
    output: "39"
    name: "Conv_2"
    op_type: "Conv"
    attribute {
      name: "dilations"
      ints: 1
      ints: 1
      type: INTS
    }
    attribute {
      name: "group"
      i: 1
      type: INT
    }
    attribute {
      name: "kernel_shape"
      ints: 9
      ints: 1
      type: INTS
    }
    attribute {
      name: "pads"
      ints: 0
      ints: 0
      ints: 0
      ints: 0
      type: INTS
    }
    attribute {
      name: "strides"
      ints: 1
      ints: 1
      type: INTS
    }
  }
  node {
    input: "39"
    input: "40"
    output: "41"
    name: "Mul_4"
    op_type: "Mul"
  }
  node {
    input: "41"
    input: "42"
    output: "43"
    na

In [9]:
showInNetron(build_dir + "/mai_subj6_export.onnx")

Serving '/workspace/finn/mai_subj6_export.onnx' at http://0.0.0.0:8081


In [10]:
from finn.util.inference_cost import inference_cost
import json

cost_dict_path = build_dir + "/mai_subj6_inference_cost.json"

inference_cost(build_dir + "/mai_subj6_export.onnx", output_json=cost_dict_path, 
               output_onnx=build_dir + "/mai_subj6_inference_cost.onnx",
               preprocess=True, discount_sparsity=True)

Inference cost for /workspace/finn/mai_subj6_export.onnx
{
  "discount_sparsity": true,
  "mem_o_FLOAT32": 1580601.0,
  "mem_w_INT8": 273036.0,
  "op_mac_FLOAT32_INT8": 57920143.0,
  "total_bops": 14827556608.0,
  "total_mem_o_bits": 50579232.0,
  "total_mem_w_bits": 2184288.0,
  "unsupported": "{'MultiThreshold'}"
}


In [11]:
from finn.core.modelwrapper import ModelWrapper
model = ModelWrapper(build_dir+"/mai_subj6_export.onnx")

In [12]:
from finn.transformation.general import GiveReadableTensorNames, GiveUniqueNodeNames, RemoveStaticGraphInputs
from finn.transformation.infer_shapes import InferShapes
from finn.transformation.infer_datatypes import InferDataTypes
from finn.transformation.fold_constants import FoldConstants

model = model.transform(InferShapes())
model = model.transform(FoldConstants())
model = model.transform(GiveUniqueNodeNames())
model = model.transform(GiveReadableTensorNames())
model = model.transform(InferDataTypes())
model = model.transform(RemoveStaticGraphInputs())

model.save(build_dir+"/mai_subj6_tidy.onnx")

In [13]:
showInNetron(build_dir + "/mai_subj6_tidy.onnx")

Stopping http://0.0.0.0:8081
Serving '/workspace/finn/mai_subj6_tidy.onnx' at http://0.0.0.0:8081


In [14]:
from finn.transformation.streamline import Streamline
from finn.transformation.streamline.reorder import MoveScalarLinearPastInvariants
import finn.transformation.streamline.absorb as absorb
from finn.transformation.streamline.reorder import MoveMaxPoolPastMultiThreshold
from finn.transformation.streamline.reorder import MakeMaxPoolNHWC
from finn.transformation.lower_convs_to_matmul import LowerConvsToMatMul
from finn.transformation.streamline.reorder import MoveTransposePastJoinAdd
from finn.transformation.streamline.reorder import MoveTransposePastScalarMul


model = ModelWrapper(build_dir+"/mai_subj6_tidy.onnx")
# streamline

model = model.transform(Streamline())
model = model.transform(LowerConvsToMatMul())
model = model.transform(MoveMaxPoolPastMultiThreshold())
model = model.transform(absorb.AbsorbTransposeIntoMultiThreshold())
model = model.transform(MakeMaxPoolNHWC())
model = model.transform(absorb.AbsorbConsecutiveTransposes())
model = model.transform(absorb.AbsorbTransposeIntoMultiThreshold())
model = model.transform(MoveTransposePastScalarMul())
#model = model.transform(MoveTransposePastJoinAdd())
model = model.transform(Streamline())

model.save(build_dir+"/mai_subj6_ready_for_hls_conversion.onnx")
showInNetron(build_dir+"/mai_subj6_ready_for_hls_conversion.onnx")

/workspace/finn/src/finn/transformation/streamline/reorder.py:1048: UserWarning: Datalayout is not set for tensors.
                            Transformation can't be applied.
  warnings.warn(


Stopping http://0.0.0.0:8081
Serving '/workspace/finn/mai_subj6_ready_for_hls_conversion.onnx' at http://0.0.0.0:8081


In [15]:
import finn.transformation.fpgadataflow.convert_to_hls_layers as to_hls
from finn.transformation.infer_data_layouts import InferDataLayouts
from finn.transformation.general import RemoveUnusedTensors
from finn.transformation.streamline.round_thresholds import RoundAndClipThresholds
from finn.transformation.infer_data_layouts import InferDataLayouts
from finn.transformation.infer_datatypes import InferDataTypes
from finn.transformation.infer_shapes import InferShapes
#from finn.transformation.fpgadataflow.convert_to_hls_layers.InferPool_Batch

model = ModelWrapper(build_dir+"/mai_subj6_ready_for_hls_conversion.onnx")
model = model.transform(to_hls.InferThresholdingLayer())

model = model.transform(to_hls.InferQuantizedStreamingFCLayer())
#model = model.transform(to_hls.InferStreamingMaxPool())
model = model.transform(to_hls.InferConvInpGen())
model = model.transform(to_hls.InferStreamingMaxPool())
#model = model.transform(to_hls.InferPool_Batch())
#model = model.transform(to_hls.InferVVAU())


model.save(build_dir+"/mai_subj6_hls_layers.onnx")
showInNetron(build_dir+"/mai_subj6_hls_layers.onnx")

Stopping http://0.0.0.0:8081
Serving '/workspace/finn/mai_subj6_hls_layers.onnx' at http://0.0.0.0:8081


/workspace/finn/src/finn/custom_op/fpgadataflow/thresholding_batch.py:125: UserWarning: inputDataType changing for Thresholding_Batch_MultiThreshold_2: INT32 -> INT24 
  warnings.warn(warn_str)
/workspace/finn/src/finn/custom_op/fpgadataflow/thresholding_batch.py:125: UserWarning: inputDataType changing for Thresholding_Batch_MultiThreshold_4: INT32 -> INT24 
  warnings.warn(warn_str)
/workspace/finn/src/finn/transformation/fpgadataflow/convert_to_hls_layers.py:64: UserWarning: Im2Col_0 : Input is not int. Can't infer ConvInpGen.
  warnings.warn(
/workspace/finn/src/finn/transformation/fpgadataflow/convert_to_hls_layers.py:64: UserWarning: Im2Col_1 : Input is not int. Can't infer ConvInpGen.
  warnings.warn(


In [16]:
model = ModelWrapper(build_dir+"/mai_subj6_hls_layers.onnx")
# streamline

# model = model.transform(Streamline())
# model = model.transform(LowerConvsToMatMul())
# #model = model.transform(MoveMaxPoolPastMultiThreshold())
# model = model.transform(absorb.AbsorbTransposeIntoMultiThreshold())
# model = model.transform(MakeMaxPoolNHWC())
model = model.transform(absorb.AbsorbConsecutiveTransposes())
# model = model.transform(absorb.AbsorbTransposeIntoMultiThreshold())
# model = model.transform(Streamline())
# model = model.transform(to_hls.InferThresholdingLayer())

# model = model.transform(to_hls.InferQuantizedStreamingFCLayer())
# #model = model.transform(to_hls.InferStreamingMaxPool())
# model = model.transform(to_hls.InferConvInpGen())
model = model.transform(to_hls.InferStreamingMaxPool())

model.save(build_dir+"/mai_subj6_additional_transformations.onnx")
showInNetron(build_dir+"/mai_subj6_additional_transformations.onnx")

Stopping http://0.0.0.0:8081
Serving '/workspace/finn/mai_subj6_additional_transformations.onnx' at http://0.0.0.0:8081


In [17]:
from finn.transformation.fpgadataflow.create_dataflow_partition import CreateDataflowPartition

model = ModelWrapper(build_dir+"/mai_subj6_hls_layers.onnx")
parent_model = model.transform(CreateDataflowPartition())
parent_model.save(build_dir+"/mai_subj6_dataflow_parent.onnx")
showInNetron(build_dir+"/mai_subj6_dataflow_parent.onnx")

Stopping http://0.0.0.0:8081
Serving '/workspace/finn/mai_subj6_dataflow_parent.onnx' at http://0.0.0.0:8081


In [18]:
from finn.custom_op.registry import getCustomOp
sdp_node = parent_model.get_nodes_by_op_type("StreamingDataflowPartition")[0]
sdp_node = getCustomOp(sdp_node)
dataflow_model_filename = sdp_node.get_nodeattr("model")
showInNetron(dataflow_model_filename)

Stopping http://0.0.0.0:8081
Serving '/tmp/finn_dev_floodd1@ad.mee.tcd.ie/dataflow_partition_nxxhpghq/partition_0.onnx' at http://0.0.0.0:8081


In [17]:
model = ModelWrapper(dataflow_model_filename)

In [18]:
fc0 = model.graph.node[0]
fc0w = getCustomOp(fc0)

print("CustomOp wrapper is of class " + fc0w.__class__.__name__)

fc0w.get_nodeattr_types()

CustomOp wrapper is of class Thresholding_Batch


{'PE': ('i', True, 0),
 'NumChannels': ('i', True, 0),
 'numSteps': ('i', True, 1),
 'ram_style': ('s', False, 'distributed', {'block', 'distributed'}),
 'inputDataType': ('s', True, ''),
 'weightDataType': ('s', True, ''),
 'outputDataType': ('s', True, ''),
 'inFIFODepth': ('i', False, 2),
 'outFIFODepth': ('i', False, 2),
 'numInputVectors': ('ints', False, [1]),
 'ActVal': ('i', False, 0),
 'mem_mode': ('s', False, 'const', {'const', 'decoupled'}),
 'runtime_writeable_weights': ('i', False, 0, {0, 1}),
 'backend': ('s', True, 'fpgadataflow'),
 'code_gen_dir_cppsim': ('s', False, ''),
 'code_gen_dir_ipgen': ('s', False, ''),
 'executable_path': ('s', False, ''),
 'ipgen_path': ('s', False, ''),
 'ip_path': ('s', False, ''),
 'ip_vlnv': ('s', False, ''),
 'exec_mode': ('s', False, '', {'', 'cppsim', 'rtlsim'}),
 'cycles_rtlsim': ('i', False, 0),
 'cycles_estimate': ('i', False, 0),
 'rtlsim_trace': ('s', False, ''),
 'res_estimate': ('s', False, ''),
 'res_hls': ('s', False, ''),
 'r

In [19]:
fc_layers = model.get_nodes_by_op_type("StreamingFCLayer_Batch")
# (PE, SIMD, in_fifo_depth, out_fifo_depth, ramstyle) for each layer
config = [
    (16, 49, 16, 64, "block"),
    (8, 8, 64, 64, "auto"),
    (8, 8, 64, 64, "auto"),
    (10, 8, 64, 10, "distributed"),
]
for fcl, (pe, simd, ififo, ofifo, ramstyle) in zip(fc_layers, config):
    fcl_inst = getCustomOp(fcl)
    fcl_inst.set_nodeattr("PE", pe)
    fcl_inst.set_nodeattr("SIMD", simd)
    fcl_inst.set_nodeattr("inFIFODepth", ififo)
    fcl_inst.set_nodeattr("outFIFODepth", ofifo)
    fcl_inst.set_nodeattr("ram_style", ramstyle)
    
# set parallelism for input quantizer to be same as first layer's SIMD
inp_qnt_node = model.get_nodes_by_op_type("Thresholding_Batch")[0]
inp_qnt = getCustomOp(inp_qnt_node)
inp_qnt.set_nodeattr("PE", 49)

In [20]:
model.save(build_dir+"/mai_subj6_set_folding_factors.onnx")
showInNetron(build_dir+"/mai_subj6_set_folding_factors.onnx")

Stopping http://0.0.0.0:8081
Serving '/workspace/finn/mai_subj6_set_folding_factors.onnx' at http://0.0.0.0:8081


In [21]:
# print the names of the supported PYNQ boards
from finn.util.basic import pynq_part_map
print(pynq_part_map.keys())

dict_keys(['Ultra96', 'Pynq-Z1', 'Pynq-Z2', 'ZCU102', 'ZCU104', 'ZCU111'])


In [24]:
# change this if you have a different PYNQ board, see list above
pynq_board = "Pynq-Z1"
fpga_part = pynq_part_map[pynq_board]
target_clk_ns = 10

In [ ]:
from finn.transformation.fpgadataflow.make_zynq_proj import ZynqBuild
model = ModelWrapper(dataflow_model_filename)
model = model.transform(ZynqBuild(platform = pynq_board, period_ns = target_clk_ns))

/workspace/finn/src/finn/transformation/fpgadataflow/floorplan.py:107: UserWarning: 28 nodes have no entry in the provided floorplan, SLR was set to -1
  warnings.warn(
/workspace/finn/src/finn/transformation/fpgadataflow/insert_fifo.py:154: UserWarning: Overriding input FIFO depth to 32
  warnings.warn("Overriding input FIFO depth to 32")
/workspace/finn/src/finn/transformation/fpgadataflow/insert_fifo.py:201: UserWarning: Overriding output FIFO depth to 32
  warnings.warn("Overriding output FIFO depth to 32")
Process ForkPoolWorker-15:
Process ForkPoolWorker-13:
Process ForkPoolWorker-16:
Process ForkPoolWorker-14:
Traceback (most recent call last):
Traceback (most recent call last):
  File "/opt/conda/lib/python3.8/multiprocessing/process.py", line 315, in _bootstrap
    self.run()
  File "/opt/conda/lib/python3.8/multiprocessing/process.py", line 315, in _bootstrap
    self.run()
  File "/opt/conda/lib/python3.8/multiprocessing/process.py", line 108, in run
    self._target(*self._

In [ ]:
model.save(build_dir + "/tfc_w1_a1_post_synthesis.onnx")